# Example: Blowfly Model
Likelihood-free inference for the blow-fly model was introduced by [Simon N.
Wood](http://dx.doi.org/10.1038/nature09319). We model here the discrete time
stochastic dynamics of the size ``N`` of an adult blowfly population as given in [section 1.2.3 of the supplementary
information](https://static-content.springer.com/esm/art%3A10.1038%2Fnature09319/MediaObjects/41586_2010_BFnature09319_MOESM302_ESM.pdf).
$$
N_{t+1} = P N_{t-\tau}\exp(-N_{t-\tau}/N_0)e_t + N_t\exp(-\delta \epsilon_t)
$$
where ``e_t`` and ``\epsilon_t`` are independent Gamma random deviates with
mean 1 and variance ``\sigma_p^2`` and ``\sigma_d^2``, respectively.

In [1]:
using Distributions, StatsBase, LikelihoodfreeInference
Base.@kwdef struct BlowFlyModel
    burnin::Int = 50
    T::Int = 1000
end
function (m::BlowFlyModel)(P, N₀, σd, σp, τ, δ)
    p1 = Gamma(1/σp^2, σp^2)
    p2 = Gamma(1/σd^2, σd^2)
    T = m.T + m.burnin + τ
    N = fill(180., T)
    for t in τ+1:T-1
        N[t+1] = P * N[t-τ] * exp(-N[t-τ]/N₀)*rand(p1) + N[t]*exp(-δ*rand(p2))
    end
    N[end-m.T+1:end]
end

Let us plot four realizations from this model with the same parameters.

In [2]:
using StatsPlots
plotly()
m = BlowFlyModel()
plot([plot(m(29, 260, .6, .3, 7, .2),
           xlabel = "t", ylabel = "N", legend = false) for _ in 1:4]...,
     layout = (2, 2))

┌ Info: For saving to png with the Plotly backend ORCA has to be installed.
└ @ Plots /home/travis/.julia/packages/Plots/cc8wh/src/backends.jl:363


Plot{Plots.PlotlyBackend() n=4}

To compare different realizations we will use histogram summary statistics.
In the literature one finds also other summary statistics for this data.

In [3]:
summary_statistics(N) = fit(Histogram, N, 140:16:16140).weights

summary_statistics (generic function with 1 method)

We will use a normal prior on log-transformed parameters.

In [4]:
function parameter(logparams)
    lP, lN₀, lσd, lσp, lτ, lδ = logparams
    (P = round(exp(2 + 2lP)),
    N₀ = round(exp(4 + .5lN₀)),
    σd = exp(-.5 + lσd),
    σp = exp(-.5 + lσp),
    τ = round(Int, max(1, min(500, exp(2 + lτ)))),
    δ = exp(-1 + .4lδ))
end
(m::BlowFlyModel)(logparams) = m(parameter(logparams)...)
target(m::BlowFlyModel) = [(log(29) - 2)/2,
                           (log(260) - 4)*2,
                           log(.6) + .5,
                           log(.3) + .5,
                           log(7) - 2,
                           (log(.2) + 1)/.4]
lower(m::BlowFlyModel) = fill(-5., 6)
upper(m::BlowFlyModel) = fill(5., 6)
prior = TruncatedMultivariateNormal(zeros(6), ones(6),
                                    lower = lower(m), upper = upper(m))

TruncatedMultivariateNormal{Distributions.MvNormal{Float64,PDMats.PDiagMat{Float64,Array{Float64,1}},Array{Float64,1}},Float64}(
mvnormal: DiagNormal(
dim: 6
μ: [0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
Σ: [1.0 0.0 … 0.0 0.0; 0.0 1.0 … 0.0 0.0; … ; 0.0 0.0 … 1.0 0.0; 0.0 0.0 … 0.0 1.0]
)

lower: [-5.0, -5.0, -5.0, -5.0, -5.0, -5.0]
upper: [5.0, 5.0, 5.0, 5.0, 5.0, 5.0]
)


Let us now generate some target data.

In [5]:
model = BlowFlyModel()
x0 = target(model)
data = summary_statistics(model(x0))

1000-element Array{Int64,1}:
 0
 0
 0
 0
 2
 0
 1
 5
 3
 1
 ⋮
 0
 0
 0
 0
 0
 0
 0
 0
 0

## Adaptive SMC

In [6]:
smc = AdaptiveSMC(prior = prior)
result = run!(smc, x -> summary_statistics(model(x)), data,
              maxfevals = 2*10^5, verbose = false)
using PrettyTables
pretty_table([[keys(parameter(zeros(6)))...] quantile(smc, .05) median(smc) mean(smc) x0 quantile(smc, .95)],
             ["names", "5%", "median", "mean", "actual", "95%"],
             formatter = ft_printf("%10.3f"))

┌───────┬────────────┬────────────┬────────────┬────────────┬────────────┐
│ names │         5% │     median │       mean │     actual │        95% │
├───────┼────────────┼────────────┼────────────┼────────────┼────────────┤
│     P │     -2.121 │      0.411 │     -0.013 │      0.684 │      2.050 │
│    N₀ │     -1.667 │     -0.023 │     -0.049 │      3.121 │      1.645 │
│    σd │     -1.708 │     -0.027 │     -0.050 │     -0.011 │      1.450 │
│    σp │     -1.650 │     -0.038 │      0.018 │     -0.704 │      2.024 │
│     τ │     -1.643 │      0.244 │      0.221 │     -0.054 │      1.767 │
│     δ │     -1.540 │      0.092 │      0.081 │     -1.524 │      1.681 │
└───────┴────────────┴────────────┴────────────┴────────────┴────────────┘


In [7]:
histogram(smc)

Plot{Plots.PlotlyBackend() n=6}

In [8]:
corrplot(smc)

┌ Warning: Keyword argument match_dimensions not supported with Plots.PlotlyBackend().  Choose from: Set(Symbol[:zforeground_color_guide, :top_margin, :group, :background_color, :yforeground_color_text, :yguidefontcolor, :seriesalpha, :legendfontcolor, :seriescolor, :ztick_direction, :zlims, :normalize, :linestyle, :xflip, :yforeground_color_guide, :fillcolor, :ygrid, :background_color_inside, :bins, :markerstrokestyle, :yscale, :clims, :xtickfontcolor, :xguide, :fillalpha, :tick_direction, :yguidefontsize, :legendfontfamily, :hover, :foreground_color, :x, :legend, :discrete_values, :ytick_direction, :ribbon, :xdiscrete_values, :orientation, :markersize, :camera, :xforeground_color_grid, :quiver, :zticks, :markerstrokecolor, :xtickfontsize, :levels, :foreground_color_border, :marker_z, :markerstrokealpha, :markeralpha, :zguidefontcolor, :ygridlinewidth, :zlink, :zscale, :smooth, :xticks, :zguidefontsize, :y, :margin, :ytickfontcolor, :title_location, :yforeground_color_border, :zguidef

Plot{Plots.PlotlyBackend() n=36}

## KernelABC

In [9]:
k = KernelABC(prior = prior, delta = 1e-1, K = 10^3, kernel = Kernel())
result = run!(k, x -> summary_statistics(model(x)), data)
pretty_table([[keys(parameter(zeros(6)))...] quantile(k, .05) median(k) mean(k) x0 quantile(k, .95)],
             ["names", "5%", "median", "mean", "actual", "95%"],
             formatter = ft_printf("%10.3f"))

┌───────┬────────────┬────────────┬────────────┬────────────┬────────────┐
│ names │         5% │     median │       mean │     actual │        95% │
├───────┼────────────┼────────────┼────────────┼────────────┼────────────┤
│     P │     -1.817 │      0.504 │      0.222 │      0.684 │      1.879 │
│    N₀ │     -1.506 │      0.146 │      0.104 │      3.121 │      1.850 │
│    σd │     -1.642 │     -0.031 │     -0.026 │     -0.011 │      1.770 │
│    σp │     -1.756 │     -0.103 │     -0.041 │     -0.704 │      1.723 │
│     τ │     -1.454 │      0.256 │      0.175 │     -0.054 │      1.732 │
│     δ │     -1.572 │      0.130 │      0.101 │     -1.524 │      1.693 │
└───────┴────────────┴────────────┴────────────┴────────────┴────────────┘


In [10]:
histogram(k)

Plot{Plots.PlotlyBackend() n=6}

## Kernel Recursive ABC (with callback)

In [11]:
k = KernelRecursiveABC(prior = prior,
                       K = 100,
                       delta = 1e-3,
                       kernel = Kernel(bandwidth = Bandwidth(heuristic = MedianHeuristic(2^3))),
                       kernelx = Kernel());

We will use a callback here to show how the estimated parameters evolves.

In [12]:
using LinearAlgebra
res_krabc = run!(k, x -> summary_statistics(model(x)), data,
                 maxfevals = 1300,
                 verbose = true,
                 callback = () -> @show norm(k.theta - x0)/norm(x0))

iteration         elapsed     fevals
norm(k.theta - x0) / norm(x0) = 0.9615619021273965
        1       0 seconds        100
norm(k.theta - x0) / norm(x0) = 0.9594880743345786
        2       2 seconds        200
norm(k.theta - x0) / norm(x0) = 0.9353777952108125
        3       3 seconds        300
norm(k.theta - x0) / norm(x0) = 0.9090988922791846
        4       4 seconds        400
norm(k.theta - x0) / norm(x0) = 0.909098892188599
        5       5 seconds        500
norm(k.theta - x0) / norm(x0) = 0.90909889427564
        6       6 seconds        600
norm(k.theta - x0) / norm(x0) = 0.9090988971032324
        7       6 seconds        700
norm(k.theta - x0) / norm(x0) = 0.9090989022140423
        8       7 seconds        800
norm(k.theta - x0) / norm(x0) = 0.9090989032291363
        9       8 seconds        900
norm(k.theta - x0) / norm(x0) = 0.9090988979809832
       10       9 seconds       1000
norm(k.theta - x0) / norm(x0) = 0.909098898655976
       11       9 seconds       1100

(x = [0.8997017696999171, 0.37054808049150834, 0.0433749868501249, 0.05667919356063706, -0.09919972736624998, 0.0800757027826376],)

---

*This notebook was generated using [Literate.jl](https://github.com/fredrikekre/Literate.jl).*